<a href="https://colab.research.google.com/github/Byeon-MJ/Computer_Vision_Project/blob/main/Video_Face_Detection_Haarcascade.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# drive mount
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [2]:
# 모듈 임포트
import cv2
import numpy as np
import time
import io
import base64
from IPython.display import HTML

In [3]:
# 원본 동영상 Display
video = io.open('/content/gdrive/MyDrive/CV/Face Detection/data/video/obama.mp4', 'r+b').read()
encoded = base64.b64encode(video)
HTML(data='''<video width="50%" controls>
            <source src = "data:video/mp4;base64,{0}" type = "video/mp4"/
            </video>'''.format(encoded.decode('ascii')))

In [4]:
# haarcascade xml 파일 위치 정의
# 얼굴 인식 feature 파일
face_cascade_name = '/content/gdrive/MyDrive/CV/Face Detection/data/haarcascades/haarcascade_frontalface_alt.xml'
# 눈 인식 feature 파일
eyes_cascade_name = '/content/gdrive/MyDrive/CV/Face Detection/data/haarcascades/haarcascade_eye_tree_eyeglasses.xml'

In [5]:
# face_cascade 인스턴트 생성
face_cascade = cv2.CascadeClassifier()

In [6]:
# eyes_cascade 인스턴트 생성
eyes_cascade = cv2.CascadeClassifier()

In [7]:
# 원본 동영상 파일 정의
file_name = 'gdrive/MyDrive/CV/Face Detection/data/video/obama.mp4'

In [8]:
# output 동영상 정의
output_name = 'output_video.mp4'

In [9]:
# 동영상에서 Face detection & Display 함수 정의
def detectAndDisplay(frame):
    # GRAY 이미지로 변환
    frame_gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    frame_gray = cv2.equalizeHist(frame_gray)
    
    # -- Detect Faces
    faces = face_cascade.detectMultiScale(frame_gray)
    for (x, y, w, h) in faces:
        center = (x + w//2, y + h//2)

        # detection 된 얼굴에 사각형 그리기
        frame = cv2.rectangle(frame, (x, y), (x+w, y+h), (0, 255, 0), 4)

        # frame_gray에서 방금 그린 얼굴 사각형 영역 가져오기(faceROI)
        faceROI = frame_gray[y:y+h, x:x+w]

        # faceROI 에서 eyes 을 detection
        eyes = eyes_cascade.detectMultiScale(faceROI)

        for (x2, y2, w2, h2) in eyes:
            eye_center = (x + x2 + w2//2, y + y2 + h2//2)
            radius = int(round((w2 + h2)*0.25)) # 반지름 계산

            # detection 된 눈에 원을 그린다.
            frame = cv2.circle(frame, eye_center, radius, (255, 0, 0 ), 4)


    # video를 output하기 위해 writer 초기화
    global writer
    
    if writer is None and output_name is not None:
        # fourcc = cv2.VideoWriter_fourcc(*"MJPG")    # 코덱 정의
        fourcc = cv2.VideoWriter_fourcc(*"DIVX")    # 코덱 정의
        writer = cv2.VideoWriter(output_name, fourcc, 30, 
                                 (frame.shape[1], frame.shape[0]), True)
        
    # disk에 frame write
    if writer is not None:
        writer.write(frame)

In [10]:
# cascades 파일 로드
if not face_cascade.load(cv2.samples.findFile(face_cascade_name)):
    print('- -(!)Error loading face cascade')
    exit(0)
if not eyes_cascade.load(cv2.samples.findFile(eyes_cascade_name)):
    print('- -(!)Error loading eyes cascade')
    exit(0)

# 원본 동영상에서 video stream을 읽어온다
cap = cv2.VideoCapture(file_name)
writer = None
if not cap.isOpened:
    print('- -(!)Error opening video capture')
    exit(0)

while True:
    ret, frame = cap.read()
    if frame is None:
        # close the video file pointers
        cap.release()
        # close the writer point
        writer.release()
        print('- -(!) No captured frame - - Break!')
        break
    detectAndDisplay(frame) # frame 을 보낸다.

- -(!) No captured frame - - Break!
